In [35]:
import glob # libreria para extraer la ruta de los archivos
import re # libreria para manejos de expresiones regulares
import collections #### para poder contar los hash
import pandas as pd # libreria para manejo de bases datos
import numpy as np # libreria para manejo de vectores y arreglos
import json #libreria para leer los metadatos guardados como un json
import operator #Libreria para organizar de mayor a menor
import matplotlib.pyplot as plt #libreria para graficas
from nltk.corpus import stopwords, wordnet # importa las stop words y las palabras del ingles
from nltk.stem.porter import PorterStemmer # metodo para stemming
from nltk.stem.lancaster import LancasterStemmer # metodo para stemming
from nltk.stem import WordNetLemmatizer # metodo para lematizar
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from nltk.tokenize import word_tokenize

In [28]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Andres\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\wordnet.zip.


True

In [18]:
#Read Files
#files_txt = glob.glob("/opt/datasets/mcda-pi1-20191/papers-txt/*.txt")
files_txt = glob.glob("C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\*") #Computer Andres

# instanciar la clase para lematizar
wordnet_lemmatizer = WordNetLemmatizer()
# llamamos al diccionario de stop words en ingles
sw = stopwords.words("english")

#leer Meta Datos
meta_data = open("xml_parser/metadata_dict.txt","r",encoding='utf-8').read()
meta_data = json.loads(meta_data)

In [29]:
documentos_text = list()
documentos      = list()
for file in files_txt:
    #Leer Informacion
    input_file = open(file,"r",encoding='utf-8')
    texto = input_file.read()
    meta_data_info = meta_data[file.replace("\\","/").split("/")[-1].replace(".txt","")]
    
    #tokenizacion
    tokens = word_tokenize(texto.lower())
    tokens = [re.sub('[^A-Za-z0-9]+','',word) for word in tokens]
    
    tokens_metada = word_tokenize(meta_data_info.lower())
    tokens_metada = [re.sub('[^A-Za-z0-9]+','',word) for word in tokens_metada]
    #mirar cant
    
    stemmer = PorterStemmer() # instancia una forma de stemming
    # aplica lematizacion, stemming, elimina de stop words y aplica reglas lógicas para reducir la cantidad de tokens
    tokens = [wordnet_lemmatizer.lemmatize(stemmer.stem(w.lower()), pos="v") for w in tokens if (len(w)>1) and (w not in sw) and wordnet.synsets(w) and w.isalpha() ] # Longitud mayor a 1
    tokens_metada = [wordnet_lemmatizer.lemmatize(stemmer.stem(w.lower()), pos="v") for w in tokens if (len(w)>1) and (w not in sw)]
    
    documentos_text.append(' '.join(tokens + tokens_metada))
    documentos.append(file)

In [30]:
vectorizer = CountVectorizer(analyzer = "word",tokenizer = word_tokenize,    \
                             preprocessor = None, \
                             stop_words = stopwords.words("english"),   \
                             lowercase = True,  \
                             max_features = None)


train_data_features = vectorizer.fit_transform(documentos_text)

In [43]:
train_data_features.shape #doc, words

(980, 14709)

In [37]:
tfidf_vectorizer=TfidfVectorizer(analyzer = "word",tokenizer = word_tokenize,    \
                             preprocessor = None, \
                             stop_words = stopwords.words("english"),   \
                             lowercase = True,  \
                             max_features = None)
 
# just send in all your docs here
tfidf_vectorizer_vectors=tfidf_vectorizer.fit_transform(documentos_text)

In [38]:
tfidf_vectorizer_vectors.shape #doc, words

(980, 14709)

In [47]:
bow_df = pd.DataFrame(train_data_features.toarray(), columns=vectorizer.get_feature_names())
bow_df.head()

aa  aaa  aachen  aalborg  aalto  aar  aarhu  aaron  ab  aba  ...    zoom  \
0   0    0       0        0      0    0      0      0   0    0  ...       0   
1   0    0       0        0      0    0      0      0   0    0  ...       0   
2   0    0       0        0      0    0      0      0   0    0  ...       0   
3   0    0       0        0      0    0      0      0   0    0  ...       0   
4   0    0       0        0      0    0      0      0   0    0  ...       0   

   zoonot  zr  zs  zu  zukerman  zulu  zurich  zweig  zygot  
0       0   0   0   0         0     0       2      0      0  
1       0   0   0   0         0     0       0      0      0  
2       0   0   0   0         0     0       0      0      0  
3       0   0   0   0         0     0       0      0      0  
4       0   0   0   0         0     0       0      0      0  

[5 rows x 14709 columns]

In [87]:
inverted_index = {}
for idx, word in enumerate(vectorizer.get_feature_names()):
    inverted_index[word] = []
    for indice_doc in train_data_features[:,idx].nonzero()[0]:
        doc = documentos[indice_doc]
        text_count = documentos_text[indice_doc].count(word)
        inverted_index[word].append( (doc, text_count) )

#aditya
#indice = vectorizer.get_feature_names().index('characterist')
#train_data_features[:,indice].nonzero()[0]
inverted_index

{'aa': [('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0903.1291.txt',
   2),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1004.0208.txt',
   4),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1006.1029.txt',
   2),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1101.1477.txt',
   2),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1104.0746.txt',
   2),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1106.1445.txt',
   44),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1110.2053.txt',
   2),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1111.0235.txt',
   20),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1111.4662.txt',
   6),
  ('C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1201.5921.txt',
   4),
  ('C:\\Users\\Andres\\Desktop\\

In [105]:
def query_inverted_text(term):
    resultado = []
    for doc, freq in inverted_index[term]:
        resultado.append(doc)
    return resultado
query_inverted_text('characterist')

#inverted_index['characterist']

['C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0808.0084.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0811.1254.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0907.3220.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0907.3965.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0910.5577.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0911.1507.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0911.1509.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0911.1544.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0911.1546.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\0911.5153.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEMESTRE_I\\texto\\papers-txt\\1006.1029.txt',
 'C:\\Users\\Andres\\Desktop\\MAESTRIA\\SEM

3

In [32]:
#print(train_data_features) #3040
for key, value in vectorizer.vocabulary_.items():
    if value == 3040:
        print(key)
        break

databa
